In [ ]:
%fs ls

path name size modificationTime dbfs:/FileStore/ FileStore/ 0 1699123086000 dbfs:/Volume/ Volume/ 0 0 dbfs:/Volumes/ Volumes/ 0 0 dbfs:/databricks-datasets/ databricks-datasets/ 0 0 dbfs:/databricks-results/ databricks-results/ 0 0 dbfs:/volume/ volume/ 0 0 dbfs:/volumes/ volumes/ 0 0

## Read Text file

In [ ]:
%fs ls /FileStore/tables/

path name size modificationTime dbfs:/FileStore/tables/Active_People.json Active_People.json 12453169 1699388512000 dbfs:/FileStore/tables/zipcodes.json zipcodes.json 7331 1699296494000

## Complex JSON file processing

In [ ]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, from_json, explode, Column
from pyspark.sql.types import StructType, StructField, StringType
from pyspark.sql.functions import monotonically_increasing_id

spark = SparkSession.builder \
            .master("local[1]") \
            .appName("ReadtxtFileExample") \
            .getOrCreate()


json_schema = StructType([StructField("items", StringType())])

json_data = spark.read \
     .option("infraSchema", "true") \
     .json("/FileStore/tables/Active_People.json")

#json_data.printSchema()

#display(json_data)

json_flaten_df = json_data.select(
                 col("items.activeId"), 
                 col("items.agencyId"), 
                 col("items.id"),
                 col("items.firstName"),
                 col("items.lastName"),
                 col("items.gender"),
                 col("items.dob"),
                 col("items.email"),
                 col("items.created"),
                 col("items.modified"),
                 
                 col("items.billingAddress.id").alias("billingAddress_id"),
                 col("items.billingAddress.addressLine1").alias("billingAddress_addressLine1"),
                 col("items.billingAddress.addressLine2").alias("billingAddress_addressLine2"),
                 col("items.billingAddress.addressType").alias("billingAddress_addressType"),
                 col("items.billingAddress.city").alias("billingAddress_city"),
                 col("items.billingAddress.contactPhone").alias("billingAddress_contactPhone"),
                 col("items.billingAddress.state").alias("billingAddress_state"),
                 col("items.billingAddress.zipCode").alias("billingAddress_zipCode"),
                 col("items.billingAddress.country").alias("billingAddress_country"),
                 col("items.billingAddress.created").alias("billingAddress_created"),
                 col("items.billingAddress.modified").alias("billingAddress_modified"),
                 
                 col("items.homeAddress.id").alias("homeAddress_id"),
                 col("items.homeAddress.addressLine1").alias("homeAddress_addressLine1"),
                 col("items.homeAddress.addressLine2").alias("homeAddress_addressLine2"),
                 col("items.homeAddress.addressType").alias("homeAddress_addressType"),
                 col("items.homeAddress.city").alias("homeAddress_city"),
                 col("items.homeAddress.contactPhone").alias("homeAddress_contactPhone"),
                 col("items.homeAddress.state").alias("homeAddress_state"),
                 col("items.homeAddress.zipCode").alias("homeAddress_zipCode"),
                 col("items.homeAddress.country").alias("homeAddress_country"),
                 col("items.homeAddress.created").alias("homeAddress_created"),
                 col("items.homeAddress.modified").alias("homeAddress_modified"),

                 col("items.shippingAddress.id").alias("shippingAddress_id"),
                 col("items.shippingAddress.addressLine1").alias("shippingAddress_addressLine1"),
                 col("items.shippingAddress.addressLine2").alias("shippingAddress_addressLine2"),
                 col("items.shippingAddress.addressType").alias("shippingAddress_addressType"),
                 col("items.shippingAddress.city").alias("shippingAddress_city"),
                 col("items.shippingAddress.contactPhone").alias("shippingAddress_contactPhone"),
                 col("items.shippingAddress.state").alias("shippingAddress_state"),
                 col("items.shippingAddress.zipCode").alias("shippingAddress_zipCode"),
                 col("items.shippingAddress.country").alias("shippingAddress_country"),
                 col("items.shippingAddress.created").alias("shippingAddress_created"),
                 col("items.shippingAddress.modified").alias("shippingAddress_modified"),
                 col("meta.totalCount").alias("total_count")
                 )

json_flaten_df.printSchema()

# Id
final_df = json_flaten_df.selectExpr("posexplode(id) as (pos, id)")
final_df=final_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

# Activity
process_df = json_flaten_df.selectExpr("posexplode(activeId) as (pos, activeId)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, process_df.activeId)

# Agency
process_df = json_flaten_df.selectExpr("posexplode(agencyId) as (pos, agencyId)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, process_df.agencyId)


# firstName
process_df = json_flaten_df.selectExpr("posexplode(firstName) as (pos, firstName)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, process_df.firstName)

# lastName
process_df = json_flaten_df.selectExpr("posexplode(lastName) as (pos, lastName)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, process_df.lastName)

# gender
process_df = json_flaten_df.selectExpr("posexplode(gender) as (pos, gender)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, process_df.gender)

# dob
process_df = json_flaten_df.selectExpr("posexplode(dob) as (pos, dob)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, process_df.dob)

# email
process_df = json_flaten_df.selectExpr("posexplode(email) as (pos, email)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, process_df.email)

# created
process_df = json_flaten_df.selectExpr("posexplode(created) as (pos, created)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select(final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, process_df.created)

# modified
process_df = json_flaten_df.selectExpr("posexplode(modified) as (pos, modified)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, process_df.modified)

# billingAddress_id
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_id) as (pos, billingAddress_id)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, process_df.billingAddress_id)

# billingAddress_addressLine1
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_addressLine1) as (pos, billingAddress_addressLine1)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, process_df.billingAddress_addressLine1)

# billingAddress_addressLine2
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_addressLine1) as (pos, billingAddress_addressLine2)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, process_df.billingAddress_addressLine2)

# billingAddress_addressType
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_addressType) as (pos, billingAddress_addressType)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, process_df.billingAddress_addressType)

# billingAddress_city
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_city) as (pos, billingAddress_city)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, process_df.billingAddress_city)

# billingAddress_contactPhone
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_contactPhone) as (pos, billingAddress_contactPhone)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, process_df.billingAddress_contactPhone)


# billingAddress_state
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_state) as (pos, billingAddress_state)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, process_df.billingAddress_state)

# billingAddress_zipCode
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_zipCode) as (pos, billingAddress_zipCode)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, process_df.billingAddress_zipCode)

# billingAddress_country
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_country) as (pos, billingAddress_country)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, process_df.billingAddress_country)

# billingAddress_created
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_created) as (pos, billingAddress_created)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, process_df.billingAddress_created)


# billingAddress_modified
process_df = json_flaten_df.selectExpr("posexplode(billingAddress_modified) as (pos, billingAddress_modified)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, process_df.billingAddress_modified)

# homeAddress_id
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_id) as (pos, homeAddress_id)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, process_df.homeAddress_id)

# homeAddress_addressLine1
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_addressLine1) as (pos, homeAddress_addressLine1)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, process_df.homeAddress_addressLine1)

# homeAddress_addressLine2
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_addressLine2) as (pos, homeAddress_addressLine2)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, process_df.homeAddress_addressLine2)


# homeAddress_addressType
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_addressType) as (pos, homeAddress_addressType)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, process_df.homeAddress_addressType)

# homeAddress_city
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_city) as (pos, homeAddress_city)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, process_df.homeAddress_city)

# homeAddress_contactPhone
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_contactPhone) as (pos, homeAddress_contactPhone)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, process_df.homeAddress_contactPhone)

# homeAddress_state
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_state) as (pos, homeAddress_state)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, process_df.homeAddress_state)

# homeAddress_zipCode
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_zipCode) as (pos, homeAddress_zipCode)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, process_df.homeAddress_zipCode)

# homeAddress_country
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_country) as (pos, homeAddress_country)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, process_df.homeAddress_country)

# homeAddress_created
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_created) as (pos, homeAddress_created)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, process_df.homeAddress_created)

# homeAddress_modified
process_df = json_flaten_df.selectExpr("posexplode(homeAddress_modified) as (pos, homeAddress_modified)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, process_df.homeAddress_modified)

# shippingAddress_id
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_id) as (pos, shippingAddress_id)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, process_df.shippingAddress_id)

# shippingAddress_addressLine1
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_addressLine1) as (pos, shippingAddress_addressLine1)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, process_df.shippingAddress_addressLine1)

# shippingAddress_addressLine2
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_addressLine2) as (pos, shippingAddress_addressLine2)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, process_df.shippingAddress_addressLine2)

# shippingAddress_addressType
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_addressType) as (pos, shippingAddress_addressType)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, process_df.shippingAddress_addressType)

# shippingAddress_city
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_city) as (pos, shippingAddress_city)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, process_df.shippingAddress_city)

# shippingAddress_contactPhone
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_contactPhone) as (pos, shippingAddress_contactPhone)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, process_df.shippingAddress_contactPhone)

# shippingAddress_state
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_state) as (pos, shippingAddress_state)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, final_df.shippingAddress_contactPhone, process_df.shippingAddress_state)

# shippingAddress_zipCode
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_zipCode) as (pos, shippingAddress_zipCode)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, final_df.shippingAddress_contactPhone, final_df.shippingAddress_state, process_df.shippingAddress_zipCode)

# shippingAddress_country
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_country) as (pos, shippingAddress_country)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, final_df.shippingAddress_contactPhone, final_df.shippingAddress_state, final_df.shippingAddress_zipCode, process_df.shippingAddress_country)

# shippingAddress_created
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_created) as (pos, shippingAddress_created)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, final_df.shippingAddress_contactPhone, final_df.shippingAddress_state, final_df.shippingAddress_zipCode, final_df.shippingAddress_country, process_df.shippingAddress_created)

# shippingAddress_modified
process_df = json_flaten_df.selectExpr("posexplode(shippingAddress_modified) as (pos, shippingAddress_modified)")
process_df=process_df.coalesce(1).withColumn("auto_id", monotonically_increasing_id())

final_df = final_df.join(process_df, (final_df.auto_id == process_df.auto_id) & (final_df.pos == process_df.pos), how="left").select   (final_df.auto_id, final_df.pos, final_df.id, final_df.activeId, final_df.agencyId, final_df.firstName, final_df.lastName, final_df.gender, final_df.dob, final_df.email, final_df.created, final_df.modified, final_df.billingAddress_id, final_df.billingAddress_addressLine1, final_df.billingAddress_addressLine2, final_df.billingAddress_addressType, final_df.billingAddress_city, final_df.billingAddress_contactPhone, final_df.billingAddress_state, final_df.billingAddress_zipCode, final_df.billingAddress_country, final_df.billingAddress_created, final_df.billingAddress_modified, final_df.homeAddress_id, final_df.homeAddress_addressLine1, final_df.homeAddress_addressLine2, final_df.homeAddress_addressType, final_df.homeAddress_city, final_df.homeAddress_contactPhone, final_df.homeAddress_state, final_df.homeAddress_zipCode, final_df.homeAddress_country, final_df.homeAddress_created, final_df.homeAddress_modified, final_df.shippingAddress_id, final_df.shippingAddress_addressLine1, final_df.shippingAddress_addressLine2, final_df.shippingAddress_addressType, final_df.shippingAddress_city, final_df.shippingAddress_contactPhone, final_df.shippingAddress_state, final_df.shippingAddress_zipCode, final_df.shippingAddress_country, final_df.shippingAddress_created, process_df.shippingAddress_modified)

# write to csv file
final_df.write.csv("/FileStore/tables/active_peoples.csv")

#final_df.show(truncate=False)
display(final_df)


root
 |-- activeId: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- agencyId: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- id: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- firstName: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- lastName: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- gender: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- dob: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- email: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- created: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- modified: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- billingAddress_id: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- billingAddress_addressLine1: array (nullab

auto_id pos id activeId agencyId firstName lastName gender dob email created modified billingAddress_id billingAddress_addressLine1 billingAddress_addressLine2 billingAddress_addressType billingAddress_city billingAddress_contactPhone billingAddress_state billingAddress_zipCode billingAddress_country billingAddress_created billingAddress_modified homeAddress_id homeAddress_addressLine1 homeAddress_addressLine2 homeAddress_addressType homeAddress_city homeAddress_contactPhone homeAddress_state homeAddress_zipCode homeAddress_country homeAddress_created homeAddress_modified shippingAddress_id shippingAddress_addressLine1 shippingAddress_addressLine2 shippingAddress_addressType shippingAddress_city shippingAddress_contactPhone shippingAddress_state shippingAddress_zipCode shippingAddress_country shippingAddress_created shippingAddress_modified 0 0 8d26e529-2d55-41c3-982a-09296a445a24 87dea386-9d2f-43a7-9bbe-d23da32c9d36 283518704 Rodrigo Davila MALE 1987-08-08T00:00:00Z corredordebolsas@gmail.com 2019-12-19T22:24:42.683Z 2023-10-26T15:42:25.077Z f937b330-847e-4430-9734-3cd52d14cde1 Samahil 257 Samahil 257 BILLING_ADDRESS Tlalpan 5545247854 CDMX 14200 MX 2019-11-28T01:32:21.957Z 2023-10-26T15:42:21.7Z 3472c1ac-d481-4657-9a21-7052c50c0f68 Samahil 257 
Jardines del Ajusco HOME_ADDRESS Tlalpan null CDMX 14200 MX 2023-10-26T15:42:25.077Z 2023-10-26T15:42:25.077Z 3472c1ac-d481-4657-9a21-7052c50c0f68 Samahil 257 
Jardines del Ajusco HOME_ADDRESS Tlalpan null CDMX 14200 MX 2023-10-26T15:42:25.077Z 2023-10-26T15:42:25.077Z 1 1 eff6b840-77ba-48f3-b547-0e84660559e7 100f4abf-95ed-4f77-9dc4-6491f97fbb72 283518704 Pedro Sousa MALE 1974-05-28T00:00:00Z pedrojgsousa@gmail.com 2017-07-19T22:38:13.17Z 2023-10-25T17:15:51.443Z ae20378b-b7db-44a8-8d22-07356654bcd2 Avenida do Parque 504 Avenida do Parque 504 BILLING_ADDRESS Porto +351961448920 Porto 4100-376 PT 2019-02-13T22:06:44.917Z 2023-10-25T17:15:48.057Z ec6c31e4-164a-4ae6-b1f0-f2635d33114e Avenida do Parque 504 null HOME_ADDRESS Porto null Porto 4100-376 PT 2023-10-25T17:15:51.443Z 2023-10-25T17:15:51.443Z ec6c31e4-164a-4ae6-b1f0-f2635d33114e Avenida do Parque 504 null HOME_ADDRESS Porto null Porto 4100-376 PT 2023-10-25T17:15:51.443Z 2023-10-25T17:15:51.443Z 2 2 737dd61b-ce43-4c17-8e85-1689addc902e 785c4f05-f912-46af-b4f0-f317cab3283f 283518704 Nuno Albuquerque MALE 1964-07-19T00:00:00Z Geral.nadv@gmail.com 2020-11-25T19:24:56.003Z 2023-10-24T09:19:16.737Z 608bd14b-4e6d-4c54-85bc-ccc789a15dbd Rua Cmt Kwenha 24/26 Rua Cmt Kwenha 24/26 BILLING_ADDRESS Luanda 917212945 Luanda 00000 AO 2019-09-11T23:41:40.323Z 2023-10-24T09:19:12.22Z 2a8c469a-c295-4fdf-a847-39f390829e52 Rua Cmt Kwenha 24/26 HOME_ADDRESS Luanda null Luanda 00000 AO 2023-10-24T09:19:16.737Z 2023-10-24T09:19:16.737Z 2a8c469a-c295-4fdf-a847-39f390829e52 Rua Cmt Kwenha 24/26 HOME_ADDRESS Luanda null Luanda 00000 AO 2023-10-24T09:19:16.737Z 2023-10-24T09:19:16.737Z 3 3 5a14182e-c0b5-4c2a-b7ff-1b52b81eb534 e8f1011d-269a-4586-946e-a0f298a4a296 283518704 Carsten Löffler MALE 1971-09-03T00:00:00Z carstenloeffler@t-online.de 2018-07-18T07:26:53.2Z 2023-10-29T16:46:59.637Z 92d0a139-0381-47dc-9f4a-bfeba1bcf3f2 Hohendorf 37a Hohendorf 37a BILLING_ADDRESS Groitzsch 4915114096105 null 04539 DE 2019-06-19T08:44:48.64Z 2023-10-29T16:46:56.017Z d777b2e7-f693-4bc5-aa77-0f65b5cd1f35 Hohendorf 37a HOME_ADDRESS Groitzsch 4915114096105 null 04539 DE 2023-10-29T16:46:59.637Z 2023-10-29T16:46:59.637Z d777b2e7-f693-4bc5-aa77-0f65b5cd1f35 Hohendorf 37a HOME_ADDRESS Groitzsch 4915114096105 null 04539 DE 2023-10-29T16:46:59.637Z 2023-10-29T16:46:59.637Z 4 4 8322e6a3-33b8-40ea-9de0-2ea084e3604b 42211566-56e9-40da-a398-0b8c43335267 283518704 Zoe Forman FEMALE 1967-03-19T00:00:00Z zoeforman@hotmail.com 2015-08-12T12:06:24.767Z 2023-10-29T10:30:29.677Z 7314b951-7526-4d66-ba58-71cf9639d87f 2 Paradise Cottages 2 Paradise Cottages BILLING_ADDRESS Calne 07766180920 Wiltshire SN11 9HD GB 2019-08-22T13:29:32.243Z 2023-10-29T10:30:24.893Z 1ff911b2-113a-483e-bdf3-ac573da

In [ ]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import posexplode

# Create a Spark session
spark = SparkSession.builder.appName("MultiColumnExplode").getOrCreate()

# Sample data
data = [(
    ["87dea386-9d2f-43a7-9bbe-d23da32c9d36","100f4abf-95ed-4f77-9dc4-6491f97fbb72","785c4f05-f912-46af-b4f0-f317cab3283f","e8f1011d-269a-4586-946e-a0f298a4a296","42211566-56e9-40da-a398-0b8c43335267","a03c66aa-8adb-4e69-a22c-d491c82221ae","5d36db05-158f-4a27-8256-9451bbd868f3","ea79a01d-cd6c-44ec-bef6-7ea84fd262ab","8009d4b1-4b56-4466-9f44-da8ebae6bfa0","96a77bf4-2ece-4513-9d98-2065539415d6","1b1bfa99-77b9-4613-a8a9-b366234a671f"],
    [283518704,283518704,283518704,283518704,283518704,283518704,283518704,283518704,283518704,283518704,283518704]
)]

# Define the schema
schema = ["activeId", "agencyId"]

# Create DataFrame
df = spark.createDataFrame(data, schema=schema)

# Display the original DataFrame
print("Original DataFrame:")
df.show(truncate=False)

# Explode the multiple array columns
df_exploded = df.selectExpr("posexplode(activeId) as (pos, exploded_activeId)")

# Display the DataFrame after exploding the multiple array columns
print("DataFrame after exploding the multiple array columns:")
df_exploded.show(truncate=False)


Original DataFrame:
+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------+
|activeId                                                                                                                                                                                                                                                                                                                                                                                                                          |agencyId         